# Segmenting and Clustering Neighborhoods in Chicago

## Applied Data Science Capstone Project

In [2]:
from PIL import Image
import requests
url = 'https://embed-fastly.wistia.com/deliveries/9f14c698315c3f88accb403ca20e5618.webp?image_crop_resized=1280x750'
im = Image.open(requests.get(url, stream=True).raw)
im

# Introduction

The culture of Chicago, Illinois is known for the invention or significant advancement of several performing arts, including improvisational comedy, house music, blues, hip hop, gospel, jazz, and soul.

The city is known for its Chicago School and Prairie School architecture. It continues to cultivate a strong tradition of classical music, popular music, dance, and performing arts, rooted in Western civilization, as well as other traditions carried forward by its African-American, Asian-American, European American, Hispanic American, and Native American citizens.

The city is additionally known for various popular culinary dishes, including deep-dish pizza, the Chicago-style hot dog and the Italian beef sandwich. Chicago's demographics show that it is a large and ethnically diverse metropolis. With its diverse culture, comes diverse food items. There are many restaurants in Chicago, each belonging to different categories like Chinese, Indian, Italian etc.

### Business Problem:

Chicago is famous for its excelllent cuisine. It's food culture includes an array of international cuisines influenced by the city's immigrant history.

Indian restaurants have become so popular in the United States now it seems that there is one on every corner, not only in major cities but also in smaller cities. Starting an Indian restaurant can be a great business opportunity, but you need to distinguish yourself from others to enjoy long-term success.

### Find a suitable location:

If you plan a real restaurant that can demand higher prices for fresh Indian Spices, delivered daily from India, focus on neighborhoods and outlets that already attract a sophisticated Indian client. If you plan a cheap buffet restaurant, points to the masses looking for affordable high-traffic locations with large shopping centers and other local points of interest. So it is evident that to survive in such competitive market it is very important to plan startegically. Various factors need to be studied inorder to decide on the Location

### Target Audience:

My Client wants to open his business in the Downtown area, so I only focus on that district during my analysis. The objective is to locate and recommend to the management which neighborhood of Chicago will be best choice to start a restaurant. The Management also expects to understand the rationale of the recommendations made.

This would interest anyone who wants to start a new restaurant in Chicago.

# Data Section

#### For this project we need the following data:
1. Chicago data that contains list Districts, Zip code and Neighbourhoods

    Data source : https://www.dreamtown.com/maps/chicago-zipcode-map
    
    Description: This data set contains the required information. And we will use this data set to explore various neighbourhoods of Chicago

2. Indian restaurants in each neighbourhood of Chicago.

    Data source : Foursquare API
    
    Description: By using this API we will get all the venues in each neighbourhood. We can filter these venues to get only Indian restaurants.
    
    Data: From Foursquare Venues Categories - https://developer.foursquare.com/docs/resources/categories Indian Cuisine category Id - 4bf58dd8d48988d10f941735

3. Geocoder Library to get the co-ordinates


# Methodology

Let us scrape the data from the web page that contains information about the districts, zip codes and neighborhoods in Chicago. Now that we have our details in place, let us add the latitude and longitude co-ordinates to our data. A sample of the final data set is shown below.

In [1]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim
import urllib.request
import json

!pip install beautifulsoup4

from bs4 import BeautifulSoup
from urllib.request import urlopen
import requests
from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.pyplot as plt
import matplotlib.colors as colors
%matplotlib inline
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes
import folium

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


In [3]:
df = pd.read_excel('Chicago_DataZip.xlsx')
df.head()

Zip Code  District        Neighborhood
0     60611  Downtown  Cathedral District
1     60605  Downtown     Central Station
2     60605  Downtown       Dearborn Park
3     60610  Downtown          Gold Coast
4     60601  Downtown                Loop

Now that we have our details in place, let us add the latitude and longitude co-ordinates to our data using geocoder.

In [4]:
#Import Geocoder Library
!pip install geocoder

import geocoder

def get_latlng(postal_code):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Chicago, Illinois'.format(postal_code))
        lat_lng_coords = g.latlng
    return lat_lng_coords

#Let's test our function
get_latlng('60611')

[41.895350000000064, -87.62277499999999]

In [6]:
postal_codes = df['Zip Code']   

lat_lang = []

for code in postal_codes.tolist():
    lat_lang.append(get_latlng(code))

df_latlang = pd.DataFrame(lat_lang, columns=['Latitude', 'Longitude'])
df['Latitude'] = df_latlang['Latitude']
df['Longitude'] = df_latlang['Longitude']
df.head()

Zip Code  District        Neighborhood   Latitude  Longitude
0     60611  Downtown  Cathedral District  41.895350 -87.622775
1     60605  Downtown     Central Station  41.869490 -87.625855
2     60605  Downtown       Dearborn Park  41.869490 -87.625855
3     60610  Downtown          Gold Coast  41.904230 -87.638225
4     60601  Downtown                Loop  41.886255 -87.622310

The geocoder has successfully assigned co-ordinates to each of our zip codes. The geographical coordinate of Chicago are 41.8755616, -87.6244212. The data now can be visualized to be represented on a map of Chicago.

We shall use Python's folium library to visualize geographic details of Chicago and its popular neighborhoods. A map of Chicago is created with its districts superimposed on top using latitude and longitude values to get the visual below.

In [7]:
address = 'Chicago, IL'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Chicago are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Chicago are 41.8755616, -87.6244212.


In [8]:
import folium
# create map of Chicago using latitude and longitude values
map_chicago = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, district, neighborhood in zip(df['Latitude'], df['Longitude'], df['District'], df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, district)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_chicago)  
    
map_chicago

In [9]:
import urllib
def getNearbyVenues(names, latitudes, longitudes, radius=5000, categoryIds=''):
    try:
        venues_list=[]
        for name, lat, lng in zip(names, latitudes, longitudes):
            #print(name)

            # create the API request URL
            url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION, lat, lng, radius, LIMIT)

            if (categoryIds != ''):
                url = url + '&categoryId={}'
                url = url.format(categoryIds)

            # make the GET request
            response = requests.get(url).json()
            results = response["response"]['venues']

            # return only relevant information for each nearby venue
            for v in results:
                success = False
                try:
                    category = v['categories'][0]['name']
                    success = True
                except:
                    pass

                if success:
                    venues_list.append([(
                        name, 
                        lat, 
                        lng, 
                        v['name'], 
                        v['location']['lat'], 
                        v['location']['lng'],
                        v['categories'][0]['name']
                    )])

        nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
        nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude',  
                  'Venue Category']
    
    except:
        print(url)
        print(response)
        print(results)
        print(nearby_venues)

    return(nearby_venues)

In [10]:
LIMIT = 500 
radius = 5000 
CLIENT_ID = '0IZLIQ3GB0GGPNSH1KFPWUNAHTME1Q0LG2TWUMZUIQCHSNG5'
CLIENT_SECRET = 'VXUZ3YRZ1UKCQZWNPXZJW2HCMAXBCG2H5IDU2EYSUIRBYMTN'
VERSION = '20181020'

Now, let us use Foursquare API to explore the districts in Chicago which already have Indian restaurants. The API returns all the Indian restaurants in Chicago and the Neighborhood that they belong to. Our analysis shows us that there are 2103 Indian cuisine restaurants in the city. The sample of the data set is as below. 

In [12]:
#https://developer.foursquare.com/docs/resources/categories
#Indian Cusine = 4bf58dd8d48988d10f941735

chicago_indian = getNearbyVenues(names=df['Neighborhood'], latitudes=df['Latitude'], longitudes=df['Longitude'], radius=1000, categoryIds='4bf58dd8d48988d10f941735')
chicago_indian.sample(7)

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
21    Dearborn Park               41.86949              -87.625855   
550     Lake Forest               41.88425              -87.632450   
1161     Long Grove               41.88425              -87.632450   
369     Bannockburn               41.88425              -87.632450   
632        Wilmette               41.88425              -87.632450   
1582       Elmhurst               41.88425              -87.632450   
541      Kenilworth               41.88425              -87.632450   

                          Venue  Venue Latitude  Venue Longitude  \
21                      Dakshin       41.876369       -87.630793   
550                Bombay Wraps       41.884088       -87.633834   
1161                  Naansense       41.880070       -87.641033   
369                   Naansense       41.880070       -87.641033   
632   Curried Mobile Food Truck       41.885562       -87.633820   
1582                     Masala       41.881260       -87.629799   
541                       Ruchi       41.884114       -87.623464   

         Venue Category  
21    Indian Restaurant  
550   Indian Restaurant  
1161  Indian Restaurant  
369   Indian Restaurant  
632          Food Truck  
1582  Indian Restaurant  
541   Indian Restaurant

In [13]:
chicago_indian.shape

(2104, 7)

This data set helps us to look at all the Indian restaurants in Chicago. We can use this to visualize the map below that displays the most popular Indian restaurants and their neighborhood. 

In [14]:
def addToMap(df, color, existingMap):
    for lat, lng, local, venue, venueCat in zip(df['Venue Latitude'], df['Venue Longitude'], df['Neighborhood'], df['Venue'], df['Venue Category']):
        label = '{} ({}) - {}'.format(venue, venueCat, local)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7).add_to(existingMap)

In [15]:
map_chicago_indian = folium.Map(location=[latitude, longitude], zoom_start=10)
addToMap(chicago_indian, 'red', map_chicago_indian)

map_chicago_indian

In [16]:
chicago_grouped = chicago_indian.groupby('Neighborhood').count()
chicago_grouped
print('There are {} uniques categories.'.format(len(chicago_indian['Venue Category'].unique())))

There are 8 uniques categories.


On further analysis, we found out that the Indian restaurants in Chicago are divided in 8 sub-categories in the Foursquare App. The 8 sub-categories are:

Indian Restaurant

South Indian Restaurant

North Indian Restaurant

Indian Pubs

Indian Chinese Restaurant

Food Truck

Halal Restaurant

Pakistani Restaurant (Why Foursquare? 😂)

We will now use one-hot encoding to cluster the neighborhoods in our web scraped data set, based on the similarity of the Indian restaurants and their sub-categories present in them. 

In [18]:
# one hot encoding
chicago_onehot = pd.get_dummies(chicago_indian[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
chicago_onehot['Neighborhood'] = chicago_indian['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [chicago_onehot.columns[-1]] + list(chicago_onehot.columns[:-1])
chicago_onehot = chicago_onehot[fixed_columns]

chicago_grp = chicago_onehot.groupby('Neighborhood').mean().reset_index()
chicago_grp.head()

Neighborhood  Food Truck  Halal Restaurant  \
0             Addison    0.045455               0.0   
1         Albany Park    0.000000               0.0   
2           Algonquin    0.045455               0.0   
3  Alta Vista Terrace    0.000000               0.0   
4       Andersonville    0.000000               0.0   

   Indian Chinese Restaurant  Indian Restaurant  North Indian Restaurant  \
0                        0.0           0.954545                      0.0   
1                        0.0           1.000000                      0.0   
2                        0.0           0.954545                      0.0   
3                        0.0           1.000000                      0.0   
4                        0.0           1.000000                      0.0   

   Pakistani Restaurant  Pub  South Indian Restaurant  
0                   0.0  0.0                      0.0  
1                   0.0  0.0                      0.0  
2                   0.0  0.0                      0.0  
3                   0.0  0.0                      0.0  
4                   0.0  0.0                      0.0

In [19]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [20]:
num_top_venues = 5

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
chicago_venues_sorted = pd.DataFrame(columns=columns)
chicago_venues_sorted['Neighborhood'] = chicago_grp['Neighborhood']

for ind in np.arange(chicago_grp.shape[0]):
    chicago_venues_sorted.iloc[ind, 1:] = return_most_common_venues(chicago_grp.iloc[ind, :], num_top_venues)

chicago_venues_sorted.head()

Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
0             Addison     Indian Restaurant               Food Truck   
1         Albany Park     Indian Restaurant  South Indian Restaurant   
2           Algonquin     Indian Restaurant               Food Truck   
3  Alta Vista Terrace     Indian Restaurant  South Indian Restaurant   
4       Andersonville     Indian Restaurant  South Indian Restaurant   

     3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  
0  South Indian Restaurant                   Pub     Pakistani Restaurant  
1                      Pub  Pakistani Restaurant  North Indian Restaurant  
2  South Indian Restaurant                   Pub     Pakistani Restaurant  
3                      Pub  Pakistani Restaurant  North Indian Restaurant  
4                      Pub  Pakistani Restaurant  North Indian Restaurant

The Machine Learning algorithm K-means clustering comes in handy now. The neighborhoods are clustered into different colors based on the similarity of the Indian restaurants in each of them. Let us visualize this on the map of Chicago.

In [21]:
# set number of clusters
kclusters = 7

chicago_grouped_clustering = chicago_grp.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(chicago_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 3, 0, 3, 3, 0, 0, 3, 0, 0], dtype=int32)

In [22]:
# add clustering labels
chicago_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

chicago_merged = df
chicago_merged = chicago_merged.join(chicago_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
chicago_merged = chicago_merged.dropna()
chicago_merged.head()

Zip Code  District        Neighborhood   Latitude  Longitude  \
0     60611  Downtown  Cathedral District  41.895350 -87.622775   
1     60605  Downtown     Central Station  41.869490 -87.625855   
2     60605  Downtown       Dearborn Park  41.869490 -87.625855   
3     60610  Downtown          Gold Coast  41.904230 -87.638225   
4     60601  Downtown                Loop  41.886255 -87.622310   

   Cluster Labels 1st Most Common Venue    2nd Most Common Venue  \
0             3.0     Indian Restaurant  South Indian Restaurant   
1             3.0     Indian Restaurant  South Indian Restaurant   
2             3.0     Indian Restaurant  South Indian Restaurant   
3             3.0     Indian Restaurant  South Indian Restaurant   
4             6.0     Indian Restaurant               Food Truck   

     3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  
0                      Pub  Pakistani Restaurant  North Indian Restaurant  
1                      Pub  Pakistani Restaurant  North Indian Restaurant  
2                      Pub  Pakistani Restaurant  North Indian Restaurant  
3                      Pub  Pakistani Restaurant  North Indian Restaurant  
4  South Indian Restaurant                   Pub     Pakistani Restaurant

In [23]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = ['red','blue','green','yellow','orange','pink','cyan']

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(chicago_merged['Latitude'], chicago_merged['Longitude'], chicago_merged['Neighborhood'], chicago_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Discussion

The algorithm has now clustered the neighborhoods based on the similarity and number of restaurants in each of them. Due to Chicago's diverse nature and the limitations of the Foursquare API, different approaches can be tried for clustering and classification studies. Moreover, it is obvious that other classification methods can yield higher quality results for this city. 

With my current budding knowledge about Data Science, I used K-means algorithm to get these results. This can be used to get a high-level understanding of the areas in where an Indian restaurant can be opened. 

# Results

The clusters in green represent similar neighborhoods with a good amount of Indian restaurants. The ones in cyan are neighborhoods having an adequate number of these Indian Restaurants. The red, blue, yellow and orange clusters have limited Indian restaurants.

Below are the neighborhood where an Indian restaurant would be successful

In [26]:
chicago_merged.loc[chicago_merged['Cluster Labels'] == 5]

Zip Code        District   Neighborhood  Latitude  Longitude  \
55     60659  Far North Side  Peterson Park  41.99044 -87.699665   

    Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
55             5.0     Indian Restaurant  Pakistani Restaurant   

        3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  
55  Indian Chinese Restaurant      Halal Restaurant  South Indian Restaurant

In [27]:
chicago_merged.loc[chicago_merged['Cluster Labels'] == 2]

Zip Code  District  Neighborhood  Latitude  Longitude  Cluster Labels  \
10     60622  Downtown  Noble Square  41.90752    -87.673             2.0   
16     60622  Downtown    River West  41.90752    -87.673             2.0   
23     60622  Downtown   Wicker Park  41.90752    -87.673             2.0   

   1st Most Common Venue 2nd Most Common Venue    3rd Most Common Venue  \
10     Indian Restaurant                   Pub  South Indian Restaurant   
16     Indian Restaurant                   Pub  South Indian Restaurant   
23     Indian Restaurant                   Pub  South Indian Restaurant   

   4th Most Common Venue    5th Most Common Venue  
10  Pakistani Restaurant  North Indian Restaurant  
16  Pakistani Restaurant  North Indian Restaurant  
23  Pakistani Restaurant  North Indian Restaurant

In [28]:
chicago_merged.loc[chicago_merged['Cluster Labels'] == 4]

Zip Code    District          Neighborhood   Latitude  Longitude  \
27     60614  North Side              Bucktown  41.922255  -87.65471   
28     60614  North Side                DePaul  41.922255  -87.65471   
36     60614  North Side     Old Town Triangle  41.922255  -87.65471   
37     60614  North Side             Park West  41.922255  -87.65471   
38     60614  North Side        Ranch Triangle  41.922255  -87.65471   
40     60614  North Side             Sheffield  41.922255  -87.65471   
42     60614  North Side           West DePaul  41.922255  -87.65471   
43     60614  North Side  Wrightwood Neighbors  41.922255  -87.65471   

    Cluster Labels 1st Most Common Venue    2nd Most Common Venue  \
27             4.0     Indian Restaurant  North Indian Restaurant   
28             4.0     Indian Restaurant  North Indian Restaurant   
36             4.0     Indian Restaurant  North Indian Restaurant   
37             4.0     Indian Restaurant  North Indian Restaurant   
38             4.0     Indian Restaurant  North Indian Restaurant   
40             4.0     Indian Restaurant  North Indian Restaurant   
42             4.0     Indian Restaurant  North Indian Restaurant   
43             4.0     Indian Restaurant  North Indian Restaurant   

      3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
27  South Indian Restaurant                   Pub  Pakistani Restaurant  
28  South Indian Restaurant                   Pub  Pakistani Restaurant  
36  South Indian Restaurant                   Pub  Pakistani Restaurant  
37  South Indian Restaurant                   Pub  Pakistani Restaurant  
38  South Indian Restaurant                   Pub  Pakistani Restaurant  
40  South Indian Restaurant                   Pub  Pakistani Restaurant  
42  South Indian Restaurant                   Pub  Pakistani Restaurant  
43  South Indian Restaurant                   Pub  Pakistani Restaurant

In [29]:
chicago_merged.loc[chicago_merged['Cluster Labels'] == 1]

Zip Code    District    Neighborhood   Latitude  Longitude  \
163     60608  South Side      Bridgeport  41.859805 -87.654565   
166     60608  South Side       Chinatown  41.859805 -87.654565   
173     60608  South Side        Lawndale  41.859805 -87.654565   
174     60608  South Side  Little Village  41.859805 -87.654565   
175     60608  South Side   McKinley Park  41.859805 -87.654565   
179     60608  South Side          Pilsen  41.859805 -87.654565   

     Cluster Labels 1st Most Common Venue    2nd Most Common Venue  \
163             1.0     Indian Restaurant  South Indian Restaurant   
166             1.0     Indian Restaurant  South Indian Restaurant   
173             1.0     Indian Restaurant  South Indian Restaurant   
174             1.0     Indian Restaurant  South Indian Restaurant   
175             1.0     Indian Restaurant  South Indian Restaurant   
179             1.0     Indian Restaurant  South Indian Restaurant   

    3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  
163                   Pub  Pakistani Restaurant  North Indian Restaurant  
166                   Pub  Pakistani Restaurant  North Indian Restaurant  
173                   Pub  Pakistani Restaurant  North Indian Restaurant  
174                   Pub  Pakistani Restaurant  North Indian Restaurant  
175                   Pub  Pakistani Restaurant  North Indian Restaurant  
179                   Pub  Pakistani Restaurant  North Indian Restaurant

# Conclusion

Our analysis set out to get the most ideal locations to open up an Indian Restaurant. The goal of our analysis was to find places that are not close to other Indian restaurants so that we can attract a good amount of customers. 

As evident from the above analysis, the green and cyan clusters have the highest amount of competition. Opening up a restaurant in these neighborhoods will be a risky job.

The red, blue, yellow and orange orange clusters is where investors should look at for setting up an Indian restaurant as there is less competition when compared to the other neighborhoods.

In [34]:
from IPython.display import Image
Image(filename='Annotation 2020-05-16 220639.png') 

The image on the above shows the neighborhoods where our analysis has predicted that Indian restaurants would be successful. The orange area would be the most ideal neighborhood according to our analysis. This analysis can be further studied by incorporating crime data, population density, ethnicity and other factors to determine the ideal neighborhood for opening up an Indian restaurant.

We have made this analysis just based on the number of Indian restaurants in the neighborhood.


# References
[1] Chicago - Wikipedia: https://en.wikipedia.org/wiki/Chicago
[2] Chicago - Dreamtown: https://www.dreamtown.com/maps/chicago-zipcode-map
[3] Foursquare API: https://foursquare.com/developers/apps
[4] Geopy Library: https://pypi.org/project/geopy/